In [1]:
#@title Platform Detection & Path Setup { display-mode: "form" }
# Purpose: Auto-detect which cloud GPU platform we are running on and set the working directory.
# Goal: Ensure all following cells know which environment and file paths to use.

import os
import sys
from pathlib import Path
import ipywidgets as widgets
from IPython.display import display

def detect_platform():
    if 'COLAB_GPU' in os.environ or 'google.colab' in sys.modules:
        return "colab", "/content"
    elif any("paperspace" in p for p in sys.path) or 'PAPERSPACE_STACK' in os.environ:
        return "paperspace", "/notebooks"
    elif "VAST_CONTAINERPATH" in os.environ:
        return "vast", os.environ.get("VAST_CONTAINERPATH", "/workspace")
    elif "LIGHTNING_WORKSPACE" in os.environ or "LIGHTNING_USER_ID" in os.environ:
        return "lightning", "/workspace"
    elif "runpod" in str(Path.home()).lower():
        return "runpod", str(Path.home())
    else:
        return "unknown", str(Path.cwd())

platform, base_dir = detect_platform()

ui_msg = {
    "colab": "Google Colab detected",
    "paperspace": "Paperspace detected",
    "vast": "Vast.ai detected",
    "lightning": "Lightning.ai detected (Conda disabled)",
    "runpod": "RunPod detected",
    "unknown": "Unknown cloud - check setup"
}
style = "color:#fff; background:#222; padding:8px 12px; border-radius:7px; font-weight:bold;"
notice = widgets.HTML(f'<span style="{style}">{ui_msg[platform]}</span>'
                      f'<br><span style="color:silver">Working directory: {base_dir}</span>')
display(notice)


HTML(value='<span style="color:#fff; background:#222; padding:8px 12px; border-radius:7px; font-weight:bold;">…

In [2]:
#@title Clone SD-Pinnokio Repository { display-mode: "form" }
# Purpose: Clone the official SD-Pinnokio GitHub repository into the correct working directory for the current platform.
# Goal: Ensure all phase scripts and app logic are available for direct import/run in this session.

import subprocess
import shutil

repo_url = "https://github.com/remphanostar/SD-Pinnokio"
repo_dir = os.path.join(base_dir, "SD-Pinnokio")

# Clean up existing folder for a fresh state (optional, safer for debug runs)
if os.path.exists(repo_dir):
    shutil.rmtree(repo_dir)

clone_cmd = ["git", "clone", "--depth", "1", repo_url, repo_dir]
result = subprocess.run(clone_cmd, capture_output=True, text=True)

if result.returncode == 0:
    msg = f"<b style='color:limegreen;'>Repo cloned to: {repo_dir}</b>"
else:
    msg = f"<b style='color:red;'>Failed to clone repo:</b><br>{result.stderr}"

display(widgets.HTML(msg))


HTML(value="<b style='color:limegreen;'>Repo cloned to: /content/SD-Pinnokio</b>")

In [7]:
#@title Load App Library & Phase Modules { display-mode: "form" }
# Purpose: Load the app library metadata from cleaned_pinokio_apps.json and dynamically set up sys.path for the phase scripts.
# Goal: Make all phases and app data available for the notebook UI/actions.

import json

# Load app library
apps_json_path = os.path.join(repo_dir, "cleaned_pinokio_apps.json")
with open(apps_json_path, "r", encoding="utf-8") as f:
    app_library = json.load(f)

# If it's a dict, convert to list of app dicts
if isinstance(app_library, dict):
    app_library = list(app_library.values())

# Dynamically add all phase folders to sys.path so we can easily import their modules
repo_phase_dir = os.path.join(repo_dir, "github_repo")
if repo_phase_dir not in sys.path:
    sys.path.insert(0, repo_phase_dir)

# For diagnostics: Show library loaded and phase scripts ready
lib_msg = f"<b style='color:#ffa500;'>App library loaded ({len(app_library)} apps found)</b><br><span style='color:silver'>Phase modules directory: {repo_phase_dir}</span>"
display(widgets.HTML(lib_msg))


HTML(value="<b style='color:#ffa500;'>App library loaded (284 apps found)</b><br><span style='color:silver'>Ph…

In [8]:
#@title Searchable App Library UI (ipywidgets) { display-mode: "form" }
# Purpose: Display a high-contrast, interactive UI to search, filter, and select Pinokio apps from the library.
# Goal: Let the user quickly find and choose any available app for install/run using tags or free text.

from collections import defaultdict

# Extract categories/tags
categories = sorted({app["category"] if "category" in app else "Uncategorized" for app in app_library if isinstance(app, dict)})
all_tags = set()
for app in app_library:
    if not isinstance(app, dict):
        continue
    tags = app.get("tags", [])
    if isinstance(tags, list):
        all_tags.update(tags)
    elif isinstance(tags, str):
        all_tags.update(t.strip() for t in tags.split(","))
all_tags = sorted(all_tags)

# Widgets for search/filter
search_box = widgets.Text(
    value="",
    placeholder="Search apps by name or description...",
    description="Search:",
    layout=widgets.Layout(width="60%")
)
category_dropdown = widgets.Dropdown(
    options=[("All categories", None)] + [(cat, cat) for cat in categories],
    description="Category:"
)
tag_dropdown = widgets.Dropdown(
    options=[("All tags", None)] + [(tag, tag) for tag in all_tags],
    description="Tag:"
)

# Results UI
results_box = widgets.VBox([])

# Filter/search logic
def filter_apps(change=None):
    text = search_box.value.lower().strip()
    cat = category_dropdown.value
    tag = tag_dropdown.value
    filtered = []
    for app in app_library:
        if not isinstance(app, dict):
            continue
        if cat and app.get("category", "") != cat:
            continue
        if tag and tag not in app.get("tags", []):
            continue
        if text:
            txt_full = " ".join([
                str(app.get("title", "")),
                str(app.get("description", "")),
                str(app.get("tags", []))
            ]).lower()
            if text not in txt_full:
                continue
        filtered.append(app)
    if not filtered:
        results_box.children = [widgets.HTML('<span style="color:#ff0044;"><b>No matching apps found.</b></span>')]
    else:
        cards = []
        for app in filtered:
            title = app.get("title", "Untitled")
            desc = app.get("description", "No description.")
            tags = ", ".join(app.get("tags", [])) if isinstance(app.get("tags", []), list) else str(app.get("tags", []))
            card = widgets.HTML(
                f"<div style='background:#111; color:#fff; padding:8px; margin-bottom:7px; border-radius:7px; border: 1px solid #333;'>"
                f"<b style='font-size:1.12em;'>{title}</b><br>"
                f"<span style='color:#bbb;'>{desc}</span><br>"
                f"<span style='color:#30d5c8; font-size:0.96em;'>Tags: {tags}</span>"
                f"</div>"
            )
            cards.append(card)
        results_box.children = cards

# Link logic
search_box.observe(filter_apps, names="value")
category_dropdown.observe(filter_apps, names="value")
tag_dropdown.observe(filter_apps, names="value")

# Layout UI
ui_section = widgets.VBox([
    widgets.HTML("<b style='font-size:1.4em;color:#fff;background:#2980b9;padding:8px 14px;border-radius:8px;'>App Library Browser</b>"),
    widgets.HBox([search_box, category_dropdown, tag_dropdown]),
    results_box
])
display(ui_section)
filter_apps()


In [9]:
#@title Installed Apps & Action Panel UI { display-mode: "form" }
# Purpose: Display a panel for installed apps & present controls to install, launch, tunnel, or configure selected apps using the phase modules.
# Goal: Let the user see which apps are installed in this session; allow seamless install/run/launch/tunnel/config based on 12-phase logic.

# Simple session memory for installed/running apps (reset every notebook restart)
installed_apps = {}
running_apps = {}

# Install/run output console
output_area = widgets.Output(layout={'border': '1px solid #333', 'padding': '6px', 'background': '#1a1a1a', 'color': '#90ee90'})

def app_install_handler(app):
    import importlib

    # Each phase has its module: analysis, dependencies, install, run, tunnel, etc.
    # Always call into the actual repo code for each phase, passing app config as needed.
    # Below logic is a minimal example; adapt as actual module/function signatures require
    analysis = importlib.import_module("phase_app_analysis")
    dependencies = importlib.import_module("phase_dependencies")
    installer = importlib.import_module("phase_install")
    runner = importlib.import_module("phase_run")
    tunneler = importlib.import_module("phase_tunnel")

    with output_area:
        output_area.clear_output()
        print(f"Starting install for {app['title']}...")

        # Phase 3: Analyze app
        analyzed = analysis.analyze_app(app)
        print("Analysis complete.")

        # Phase 4: Install dependencies
        dependencies.install_dependencies(analyzed)
        print("Dependencies installed.")

        # Phase 5: Install app
        installer.install_app(analyzed)
        print("App installed.")

        installed_apps[app['title']] = app
        print("\nInstalled successfully!")

def app_launch_handler(app):
    import importlib
    runner = importlib.import_module("phase_run")
    tunneler = importlib.import_module("phase_tunnel")
    from random import randint
    with output_area:
        output_area.clear_output()
        print(f"Launching app: {app['title']}")
        process = runner.launch_app(app)
        running_apps[app['title']] = process
        print("App launched.")

        # Try to open tunnel if available
        tunnel_url = tunneler.open_tunnel(app)
        if tunnel_url:
            print(f"Tunnel active and sharable: {tunnel_url}")
        else:
            print("No web UI/tunnel available for this app.")

def refresh_installed_panel():
    if not installed_apps:
        installed_box.children = [widgets.HTML("<span style='color:#FFA500;'>No apps installed yet this session.</span>")]
    else:
        children = []
        for app in installed_apps.values():
            title = app.get("title", "Untitled")
            btn_launch = widgets.Button(description="Launch/Share", button_style='success')
            btn_launch.on_click(lambda e, app=app: app_launch_handler(app))

            config_btn = widgets.Button(description="Configure", button_style='info')
            # Add config logic as needed
            children.append(widgets.HBox([
                widgets.HTML(f"<span style='color:#fff;font-weight:bold;'>{title}</span>"),
                btn_launch, config_btn
            ]))
        installed_box.children = children

# UI for installable apps (search/filtered)
def make_install_buttons():
    filtered = []
    for app in app_library:
        title = app.get("title", "Untitled")
        btn_install = widgets.Button(description=f"Install '{title}'", button_style='primary')
        btn_install.on_click(lambda e, app=app: app_install_handler(app))
        filtered.append(btn_install)
    install_buttons_box.children = filtered

installed_box = widgets.VBox([])
install_buttons_box = widgets.VBox([])

# Show installed/running/app action panel
action_panel = widgets.VBox([
    widgets.HTML('<b style="font-size:1.4em;color:#fff;background:#8e44ad;padding:8px 14px;border-radius:8px;">Installed Apps & Actions</b>'),
    installed_box,
    install_buttons_box,
    output_area
])
display(action_panel)

refresh_installed_panel()
make_install_buttons()


ModuleNotFoundError: No module named 'phase_app_analysis'

In [10]:
#@title Full 12-Phase Install/Launch Cycle (One Click) { display-mode: "form" }
# Purpose: Bundle every phase (detection, analysis, deps, install, run, tunnel, optimize, etc.) into a single function for installing and launching any app using just the repo's logic.
# Goal: Guarantee that every app install/launch passes through all 12 Pinokio phases strictly as designed.

def full_12phase_cycle(app):
    import importlib

    phases = [
        "phase_platform_detection",   # Phase 1: Platform detection & env
        "phase_env_management",       # Phase 2: Environment, venv, file mgmt, shell, var
        "phase_app_analysis",         # Phase 3: Install method analysis, dependency type, webui, tunnel
        "phase_dependencies",         # Phase 4: Install python/npm/system deps
        "phase_install",              # Phase 5: App install (install.js, install.json, custom/script)
        "phase_run",                  # Phase 6: Run process management/monitoring
        "phase_tunnel",               # Phase 7: Tunnel & external URL/QR
        "phase_platform_specific",    # Phase 8: Platform cloud adaptation/optim
        "phase_optimize",             # Phase 9: Resource optimization
        "phase_test",                 # Phase 10: Test & integrity check
        "phase_notebook_ui",          # Phase 11: Notebook UI glue
        "phase_finalize"              # Phase 12: Cleanup & polish
    ]

    phase_modules = [importlib.import_module(name) for name in phases]

    with output_area:
        output_area.clear_output()
        print(f"Starting full install/launch for: {app['title']}\n")
        ctx = {"platform": platform, "base_dir": base_dir, "app_meta": app}
        for i, mod in enumerate(phase_modules, 1):
            if hasattr(mod, 'run_phase'):
                print(f"Phase {i}: {mod.__name__.replace('phase_', '').title()}...")
                ctx = mod.run_phase(ctx)
            else:
                print(f"[SKIP] {mod.__name__} has no `run_phase(ctx)`")

        print("\nALL 12 PHASES COMPLETE.\n")
        # Final tunnel/share link if produced
        share_url = ctx.get("tunnel_url") or ctx.get("webui_url")
        if share_url:
            display(widgets.HTML(
                f"<b style='color:limegreen;'>Public WebUI/Tunnel: </b><a href='{share_url}' target='_blank' style='color:#40f'>{share_url}</a>"
            ))
        else:
            print("No public tunnel or external UI detected.")
        installed_apps[app['title']] = app
        running_apps[app['title']] = ctx.get("process", None)

# Add a dedicated button for the library UI to trigger 12-phase install/run for chosen app
def get_install_run_button(app):
    btn = widgets.Button(description="🚀 1-Click Install & Launch", button_style='danger')
    btn.on_click(lambda e: full_12phase_cycle(app))
    return btn

# (For library browser results, you can append this button per app display.)


In [11]:
#@title Unified App Library + Install/Launch Panel (All-in-One Cell) { display-mode: "form" }
# Purpose: Display/search/filter all apps, and offer per-app action buttons to install/launch (runs proper 12-phase execution).
# Goal: Single UI for finding, installing, launching, and monitoring any Pinokio app—always displaying real metadata.

import ipywidgets as widgets
from IPython.display import display
from functools import partial

# -- App data handling --
# Filter out non-dict/empty
apps = [app for app in app_library if isinstance(app, dict)]
for app in apps:
    if not app.get("title"):
        # Try to derive a title from repo, name, or fallback to ID
        app["title"] = app.get("name") or app.get("repo", "").split("/")[-1].replace("-", " ").title() or "Unknown"

categories = sorted({app.get("category", "Uncategorized") for app in apps})
all_tags = set()
for app in apps:
    tags = app.get("tags", [])
    if isinstance(tags, list):
        all_tags.update(tags)
    elif isinstance(tags, str):
        all_tags.update([t.strip() for t in tags.split(",")])
all_tags = sorted(all_tags)

# -- Widget building --
search_box = widgets.Text(
    value="",
    placeholder="Search apps by name or description...",
    description="Search:",
    layout=widgets.Layout(width="50%")
)
category_dropdown = widgets.Dropdown(
    options=[("All categories", None)] + [(cat, cat) for cat in categories],
    description="Category:"
)
tag_dropdown = widgets.Dropdown(
    options=[("All tags", None)] + [(tag, tag) for tag in all_tags],
    description="Tag:"
)

output_area = widgets.Output(layout={'border': '1px solid #333', 'padding': '6px', 'background': '#1a1a1a', 'color': '#90ee90'})
state_label = widgets.HTML("")

# Simple in-memory (per session) record for installed/running
installed_titles = set()
running_titles = set()

def full_12phase_cycle(app):
    import importlib
    state_label.value = f"<b style='color:#0af;'>Working: {app['title']}</b>"
    state_label.layout.visibility = "visible"
    phases = [
        "phase_platform_detection", "phase_env_management", "phase_app_analysis",
        "phase_dependencies", "phase_install", "phase_run", "phase_tunnel",
        "phase_platform_specific", "phase_optimize", "phase_test", "phase_notebook_ui", "phase_finalize"
    ]
    phase_modules = [importlib.import_module(name) for name in phases]
    ctx = {"platform": platform, "base_dir": base_dir, "app_meta": app}
    with output_area:
        output_area.clear_output()
        print(f"Starting full install/launch for: {app['title']}\n")
        for i, mod in enumerate(phase_modules, 1):
            phasefunc = getattr(mod, "run_phase", None)
            if phasefunc:
                print(f"Phase {i}: {mod.__name__.replace('phase_', '').title()}...")
                ctx = phasefunc(ctx)
        print("\nALL 12 PHASES COMPLETE.\n")
        share_url = ctx.get("tunnel_url") or ctx.get("webui_url")
        if share_url:
            display(widgets.HTML(
                f"<b style='color:limegreen;'>Public WebUI/Tunnel: </b><a href='{share_url}' target='_blank' style='color:#40f'>{share_url}</a>"
            ))
        else:
            print("No public tunnel or external UI detected.")
        installed_titles.add(app['title'])
        running_titles.add(app['title'])
        state_label.value = f"<b style='color:limegreen;'>Installed & running: {app['title']}</b>"
        state_label.layout.visibility = "visible"

def filter_apps(change=None):
    text = search_box.value.lower().strip()
    cat = category_dropdown.value
    tag = tag_dropdown.value
    filtered = []
    for app in apps:
        if cat and app.get("category", "") != cat:
            continue
        if tag and tag not in app.get("tags", []):
            continue
        if text:
            txt_full = " ".join([
                str(app.get("title", "")),
                str(app.get("description", "")),
                str(app.get("tags", []))
            ]).lower()
            if text not in txt_full:
                continue
        filtered.append(app)
    # Panel
    if not filtered:
        app_vbox.children = [widgets.HTML('<span style="color:#ff0044;"><b>No matching apps.</b></span>')]
    else:
        panels = []
        for app in filtered:
            title = app.get("title", "Untitled")
            desc = app.get("description", "No description.")
            tags = ", ".join(app.get("tags", [])) if isinstance(app.get("tags", []), list) else str(app.get("tags", []))
            install_btn = widgets.Button(
                description="Install" if title not in installed_titles else "Reinstall",
                button_style="primary", layout=widgets.Layout(width="100px")
            )
            install_btn.on_click(partial(lambda b, a: full_12phase_cycle(a), a=app))
            launch_label = ""
            if title in running_titles:
                launch_label = "<b style='color:limegreen;'>Running</b>"
            panel = widgets.HBox([
                widgets.VBox([
                    widgets.HTML(f"<div style='background:#1a1a1a; color:#fff; padding:8px; border-radius:5px;'><b style='font-size:1.11em;'>{title}</b>"
                                 f"<br><span style='color:#bbb;'>{desc}</span></div>"),
                    widgets.HTML(f"<span style='color:#30d5c8; font-size:0.96em;'>Tags: {tags}&nbsp;&nbsp;{launch_label}</span>")
                ]),
                install_btn
            ])
            panels.append(panel)
        app_vbox.children = panels

# UI container
app_vbox = widgets.VBox([])
search_box.observe(filter_apps, names="value")
category_dropdown.observe(filter_apps, names="value")
tag_dropdown.observe(filter_apps, names="value")

ui = widgets.VBox([
    widgets.HTML("<b style='font-size:1.4em; color:#fff; background:#2980b9; padding:8px 14px; border-radius:8px;'>Pinokio App Control Center</b>"),
    widgets.HBox([search_box, category_dropdown, tag_dropdown]),
    state_label,
    app_vbox,
    output_area
])
display(ui)
filter_apps()


ModuleNotFoundError: No module named 'phase_platform_detection'

ModuleNotFoundError: No module named 'phase_platform_detection'